In [1]:
#encoding=utf8
import os
import pickle
from itertools import chain
import numpy as np
import pandas as pd
from sklearn.model_selection import train_test_split
from sentence import Sentence
from sentence import TagPrefix
from sentence import TagSurfix

In [9]:
import os

rootDir='.\corpus'
for dirName, subdirList, fileList in os.walk(rootDir):
    for file in fileList:
        if file.endswith(".txt"):
            curFile = os.path.join(dirName, file)
            with open(curFile, "r", encoding='utf-8') as fp:
                for line in fp.readlines():
                    print(line)

人民网/nz 1月1日/t 讯/ng 据/p 《/w [纽约/nsf 时报/n]/nz 》/w 报道/v ，/w 美国/nsf 华尔街/nsf 股市/n 在/p 2013年/t 的/ude1 最后/f 一天/mq 继续/v 上涨/vn ，/w 和/cc [全球/n 股市/n]/nz 一样/uyy ，/w 都/d 以/p [最高/a 纪录/n]/nz 或/c 接近/v [最高/a 纪录/n]/nz 结束/v 本/rz 年/qt 的/ude1 交易/vn 。/w 

《/w [纽约/nsf 时报/n]/nz 》/w 报道/v 说/v ，/w 标普/nz 500/m 指数/n 今年/t 上升/vi 29.6%/m ，/w 为/p 1997年/t 以来/f 的/ude1 最大/gm 涨幅/n ；/w [道琼斯/ntc 工业/n 平均/a 指数/n]/nz 上升/vi 26.5%/m ，/w 为/p 1996年/t 以来/f 的/ude1 最大/gm 涨幅/n ；/w [纳斯/nrf 达/v 克/q]/nz 上涨/vi 38.3%/m 。/w 

就/d 12月31日/t 来说/uls ，/w 由于/p 就业/vn 前景/n 看好/v 和/cc [经济/n 增长/v]/nz 明年/t 可能/v 加速/vn ，/w 消费者/n 信心/n 上升/vi 。/w 工商/n 协进会/nis （/w ConferenceBoard/x ）/w 报告/n ，/w 12月/t 消费者/n 信心/n 上升/vi 到/v 78.1/m ，/w 明显/a 高于/v 11月/t 的/ude1 72/m 。/w 

另据/nz 《/w [华尔街/nsf 日报/n]/nz 》/w 报道/v ，/w 2013年/t 是/vshi 1995年/t 以来/f [美国/nsf 股市/n]/nz 表现/v 最好/d 的/ude1 一年/mq 。/w 这/rzv 一年/mq 里/f ，/w 投资/v [美国/nsf 股市/n]/nz 的/ude1 明智/a 做法/n 是/vshi 追/v 着/uzhe “/w 傻钱/nz ”/w 跑/v 。/w 所谓/v 的/ude1 “/w 傻钱/nz ”/w 策略/n ，/w 其实/d 就是/v 买入/vn 并/cc 持有/v 美国/nsf 股票/n 这样/rzv 的/ude1

In [5]:
class DataHandler(object):
    def __init__(self, rootDir='raw_data', save_path='data/data.pkl'):
        self.rootDir = rootDir
        self.save_path = save_path
        self.spiltChar = ['。', '!', '！', '？', '?']
        self.max_len = 200
        self.totalLine = 0
        self.longLine = 0
        self.totalChars = 0
        self.TAGPRE = TagPrefix.convert()

    # 判断数据是否预处理
    def loadData(self):
        isFile = os.path.isfile(self.save_path)
        # 导入数据
        if isFile:
            with open(self.save_path, 'rb') as inp:
                self.X = pickle.load(inp)
                self.y = pickle.load(inp)
                self.word2id = pickle.load(inp)
                self.id2word = pickle.load(inp)
                self.tag2id = pickle.load(inp)
                self.id2tag = pickle.load(inp)
        else:
            self.loadRawData()
            self.handlerRawData()

    # 顺序读取文件，按行处理
    def loadRawData(self):
        self.datas = list()
        self.labels = list()
        if self.rootDir:
            print(self.rootDir)
            for dirName, subdirList, fileList in os.walk(self.rootDir):
                # curDir = os.path.join(self.rootDir, dirName)
                for file in fileList:
                    if file.endswith(".txt"):
                        curFile = os.path.join(dirName, file)
                        print("processing:%s" % (curFile))
                        with open(curFile, "r", encoding='utf-8') as fp:
                            for line in fp.readlines():
                                self.processLine(line)

            print("total:%d, long lines:%d, total chars:%d" % (self.totalLine, self.longLine, self.totalChars))
            print('Length of datas is %d' % len(self.datas))
            print('Example of datas: ', self.datas[0])
            print('Example of labels:', self.labels[0])

    # 处理一行记录
    def processLine(self, line):
        line = line.strip()  # 去除掉前后空格
        nn = len(line)
        seeLeftB = False  # [纽约/nsf 时报/n]/nz 这种类型数据的开始标记，当为True时，代表后续的是这样的数据类型
        start = 0
        sentence = Sentence()  # 代表一个句子
        try:
            for i in range(nn):  # 循环遍历整个句子
                if line[i] == ' ':  # 一个token的结束
                    if not seeLeftB:
                        token = line[start:i]
                        if token.startswith('['):
                            tokenLen = len(token)
                            while tokenLen > 0 and token[tokenLen - 1] != ']':
                                tokenLen = tokenLen - 1
                            token = token[1:tokenLen - 1]
                            ss = token.split(' ')
                            for s in ss:  # 把[纽约/nsf 时报/n]/nz 中的两个子token分别做处理
                                self.processToken(s, sentence, False)
                        else:
                            self.processToken(token, sentence, False)
                        start = i + 1
                elif line[i] == '[':
                    seeLeftB = True
                elif line[i] == ']':
                    seeLeftB = False

            if start < nn:  # 该句子中最后一个token
                token = line[start:]
                if token.startswith('['):
                    tokenLen = len(token)
                    while tokenLen > 0 and token[tokenLen - 1] != ']':
                        tokenLen = tokenLen - 1
                    token = token[1:tokenLen - 1]
                    ss = token.split(' ')
                    ns = len(ss)
                    for i in range(ns - 1):
                        self.processToken(ss[i], sentence, False)
                    self.processToken(ss[-1], sentence, True)
                else:
                    self.processToken(token, sentence, True)
        except Exception as e:
            print('处理数据异常, 异常行为：' + line)
            print(e)

    # 代表处理一个单词、一个token
    def processToken(self, tokens, sentence, end):
        nn = len(tokens)
        while nn > 0 and tokens[nn - 1] != '/':
            nn = nn - 1

        token = tokens[:nn - 1].strip()  # 实际的token值
        tagPre = tokens[nn:].strip()  # 该token所对应的标记
        tagPre = self.TAGPRE.get(tagPre, TagPrefix.general.value) # 把原始语料的标记进行转换训练所需的标记
        if token not in self.spiltChar:
            sentence.addToken(token, tagPre)
        if token in self.spiltChar or end:
            if sentence.chars > self.max_len:  # 大于最大长度则直接过滤掉
                self.longLine += 1
            else:
                x = []
                y = []
                self.totalChars += sentence.chars
                sentence.generate_tr_line(x, y)

                if len(x) > 0 and len(x) == len(y):
                    self.datas.append(x)
                    self.labels.append(y)
                else:
                    print('处理一行数据异常, 异常行如下')
                    print(sentence.tokens)
            self.totalLine += 1
            sentence.clear()

    # 制作word2id  id2word 等
    def handlerRawData(self):
        self.df_data = pd.DataFrame({'words': self.datas, 'tags': self.labels}, index=range(len(self.datas)))
        # 　句子长度
        self.df_data['sentence_len'] = self.df_data['words'].apply(
            lambda words: len(words))  # 计算每个单词的长度，放到sentence_len列中

        # 1.用 chain(*lists) 函数把多个list拼接起来
        all_words = list(chain(*self.df_data['words'].values))
        # 2.统计所有 word
        sr_allwords = pd.Series(all_words)
        sr_allwords = sr_allwords.value_counts()  # 按照每个字

        set_words = sr_allwords.index
        set_ids = range(1, len(set_words) + 1)  # 注意从1开始，因为我们准备把0作为填充值
        # tags = ['x', 's', 'b', 'm', 'e']
        tags = ['x']  # padding的时候对应的标签

        for _, memberPre in TagPrefix.__members__.items():
            for _, memberSuf in TagSurfix.__members__.items():
                if memberSuf is TagSurfix.S and memberPre is TagPrefix.general:
                    tags.append(memberPre.value + memberSuf.value)
                elif memberSuf != TagSurfix.S:
                    tags.append(memberPre.value + memberSuf.value)

        print(tags)

        tag_ids = range(len(tags))

        # 3. 构建 words 和 tags 都转为数值 id 的映射（使用 Series 比 dict 更加方便）
        self.word2id = pd.Series(set_ids, index=set_words)
        self.id2word = pd.Series(set_words, index=set_ids)
        self.id2word[len(set_ids) + 1] = '<NEW>'  # 添加一个未知字符的支持
        self.word2id['<NEW>'] = len(set_ids) + 1

        self.tag2id = pd.Series(tag_ids, index=tags)
        self.id2tag = pd.Series(tags, index=tag_ids)

        self.df_data['X'] = self.df_data['words'].apply(self.X_padding)
        self.df_data['y'] = self.df_data['tags'].apply(self.y_padding)

        # 最后得到了所有的数据
        self.X = np.asarray(list(self.df_data['X'].values))
        self.y = np.asarray(list(self.df_data['y'].values))
        print('X.shape={}, y.shape={}'.format(self.X.shape, self.y.shape))
        print('Example of words: ', self.df_data['words'].values[0])
        print('Example of X: ', self.X[0])
        print('Example of tags: ', self.df_data['tags'].values[0])
        print('Example of y: ', self.y[0])

        # 保存数据
        with open(self.save_path, 'wb') as outp:
            pickle.dump(self.X, outp)
            pickle.dump(self.y, outp)
            pickle.dump(self.word2id, outp)
            pickle.dump(self.id2word, outp)
            pickle.dump(self.tag2id, outp)
            pickle.dump(self.id2tag, outp)
        print('** Finished saving the data.')

    def X_padding(self, words):
        """把 words 转为 id 形式，并自动补全位 max_len 长度。"""
        ids = list(self.word2id[words])
        if len(ids) >= self.max_len:  # 长则弃掉
            return ids[:self.max_len]
        ids.extend([0] * (self.max_len - len(ids)))  # 短则补全
        return ids

    def y_padding(self, tags):
        """把 tags 转为 id 形式， 并自动补全位 max_len 长度。"""
        ids = list(self.tag2id[tags])
        if len(ids) >= self.max_len:  # 长则弃掉
            return ids[:self.max_len]
        ids.extend([0] * (self.max_len - len(ids)))  # 短则补全
        return ids

    # 划分训练集、测试集、验证集
    def builderTrainData(self):
        X_train, X_test, y_train, y_test = train_test_split(self.X, self.y, test_size=0.2, random_state=42)
        X_train, X_valid, y_train, y_valid = train_test_split(X_train, y_train, test_size=0.2, random_state=42)
        print(
            'X_train.shape={}, y_train.shape={}; \nX_valid.shape={}, y_valid.shape={};\nX_test.shape={}, y_test.shape={}'.format(
                X_train.shape, y_train.shape, X_valid.shape, y_valid.shape, X_test.shape, y_test.shape))

        print('Creating the data generator ...')
        data_train = BatchGenerator(X_train, y_train, shuffle=True)
        data_valid = BatchGenerator(X_valid, y_valid, shuffle=False)
        data_test = BatchGenerator(X_test, y_test, shuffle=False)
        print('Finished creating the data generator.')

        return data_train, data_valid, data_test

In [10]:
data = DataHandler(rootDir='.\corpus', save_path='data\\test.pkl')
data.loadData()

.\corpus
processing:.\corpus\c1002-23995935.txt
processing:.\corpus\c1002-23996898.txt
processing:.\corpus\c1002-23997103.txt
processing:.\corpus\c1002-23997165.txt
total:43, long lines:0, total chars:1875
Length of datas is 43
Example of datas:  ['人', '民', '网', '1', '月', '1', '日', '讯', '据', '《', '纽', '约', '时', '报', '》', '报', '道', '，', '美', '国', '华', '尔', '街', '股', '市', '在', '2', '0', '1', '3', '年', '的', '最', '后', '一', '天', '继', '续', '上', '涨', '，', '和', '全', '球', '股', '市', '一', '样', '，', '都', '以', '最', '高', '纪', '录', '或', '接', '近', '最', '高', '纪', '录', '结', '束', '本', '年', '的', '交', '易']
Example of labels: ['b', 'm', 'e', 'Date_b', 'Date_m', 'Date_m', 'Date_e', 's', 's', 's', 'b', 'e', 'b', 'e', 's', 'b', 'e', 's', 'b', 'e', 'b', 'm', 'e', 'b', 'e', 's', 'Date_b', 'Date_m', 'Date_m', 'Date_m', 'Date_e', 's', 'b', 'e', 'b', 'e', 'b', 'e', 'b', 'e', 's', 's', 'b', 'e', 'b', 'e', 'b', 'e', 's', 's', 's', 'b', 'e', 'b', 'e', 's', 'b', 'e', 'b', 'e', 'b', 'e', 'b', 'e', 's', 's', 's', 'b', 'e

# POS数据集拆分features&labels

In [1]:
import os,re
import pandas as pd
import numpy as np
import pickle

In [2]:
pos = pd.read_csv('./pos.csv')
vocab_to_int_l = {label: ii for ii, label in enumerate(list(pos['POS']),1)}
len(vocab_to_int_l)

148

In [3]:
class DataHandler(object):
    def __init__(self, rootDir='E:\\workspace\\python_space\\2014'):
  
        self.rootDir = rootDir
        
        
    def loadRawData(self):
        self.all_sentences = list() # 全文词集合(有一定格式)
        self.all_labels = list() # 全文词性集合(有一定格式)
        self.labels = list() # 为全文词性统计
        self.words = list() # 为全文字统计
        
        if self.rootDir:
            for dirName, subdirList, fileList in os.walk(self.rootDir):
                for file in fileList:
                    if file.endswith(".txt"):
                        
                        curFile = os.path.join(dirName, file)
                        print("processing:%s" % (curFile))
                        with open(curFile, "r", encoding='utf-8') as fp:                            
                            for line in fp.readlines(): # 段
                                if len(line) > 1: # 消除空句影响
                                    line = line.strip()
                                    self.processLine(line)
               
            print('number of words is %d' % len(self.words))
            print('number of sentences is %d' % len(self.all_sentences))
            print('Example of sentences: ', self.all_sentences[9])
            print('Example of labels:', self.all_labels[9])
            
    # 处理人民日报'['、']'等无效符号         
    def processLine(self,line):
        self.sentence = list() # 句集合
        self.label_p_sent = list() # 句词性集合
                
        word = line.split(' ')        
        if len(word) > 1:
            for i in word:
                if len(i) > 1:
                    i = i.replace('[','').replace(']','')
                    
                    token = i.split('/')
                    if len(token) > 1:
                        self.words.append(token[0]) # 为实现字计数以及word2int
                        self.sentence.append(token[0])
                        if token[1] in vocab_to_int_l:
                            self.labels.append(token[1]) # 为实现词性计数以及label2int                    
                            self.label_p_sent.append(token[1])
                        else:
                            self.labels.append('n') # 容忍性错标，已统计错标率非常小，不影响训练误差。                   
                            self.label_p_sent.append('n')
        
        self.all_sentences.append(self.sentence)
        self.all_labels.append(self.label_p_sent)

In [4]:
data = DataHandler()
data.loadRawData()

processing:E:\workspace\python_space\2014\0101\c1002-23995935.txt
processing:E:\workspace\python_space\2014\0101\c1002-23996693.txt
processing:E:\workspace\python_space\2014\0101\c1002-23996898.txt
processing:E:\workspace\python_space\2014\0101\c1002-23997103.txt
processing:E:\workspace\python_space\2014\0101\c1002-23997165.txt
processing:E:\workspace\python_space\2014\0101\c1002-23997261.txt
processing:E:\workspace\python_space\2014\0101\c1003-23996577.txt
processing:E:\workspace\python_space\2014\0101\c138901-20279730.txt
processing:E:\workspace\python_space\2014\0101\c138901-20279758.txt
processing:E:\workspace\python_space\2014\0101\c138901-20279774.txt
processing:E:\workspace\python_space\2014\0101\c138901-20279841.txt
processing:E:\workspace\python_space\2014\0101\c138901-20279846.txt
processing:E:\workspace\python_space\2014\0101\c138901-20279957.txt
processing:E:\workspace\python_space\2014\0101\c138901-20280040.txt
processing:E:\workspace\python_space\2014\0101\c138901-2028006

processing:E:\workspace\python_space\2014\0101\c188534-20280624.txt
processing:E:\workspace\python_space\2014\0101\c188534-20280626.txt
processing:E:\workspace\python_space\2014\0101\c188534-20280629.txt
processing:E:\workspace\python_space\2014\0101\c188534-20280632.txt
processing:E:\workspace\python_space\2014\0101\c188534-20280639.txt
processing:E:\workspace\python_space\2014\0101\c188534-20280659.txt
processing:E:\workspace\python_space\2014\0101\c188539-20280670.txt
processing:E:\workspace\python_space\2014\0101\c188539-20280942.txt
processing:E:\workspace\python_space\2014\0101\c188539-20280955.txt
processing:E:\workspace\python_space\2014\0101\c188539-20280960.txt
processing:E:\workspace\python_space\2014\0101\c188539-20280961.txt
processing:E:\workspace\python_space\2014\0101\c190198-20279358.txt
processing:E:\workspace\python_space\2014\0101\c190198-20279949.txt
processing:E:\workspace\python_space\2014\0101\c190198-20280141.txt
processing:E:\workspace\python_space\2014\0101\c

processing:E:\workspace\python_space\2014\0101\c231182-20280628.txt
processing:E:\workspace\python_space\2014\0101\c231182-20280973.txt
processing:E:\workspace\python_space\2014\0101\c231183-20279738.txt
processing:E:\workspace\python_space\2014\0101\c231183-20279761.txt
processing:E:\workspace\python_space\2014\0101\c231183-20279770.txt
processing:E:\workspace\python_space\2014\0101\c231183-20279815.txt
processing:E:\workspace\python_space\2014\0101\c231183-20280405.txt
processing:E:\workspace\python_space\2014\0101\c231183-20280433.txt
processing:E:\workspace\python_space\2014\0101\c231183-20280478.txt
processing:E:\workspace\python_space\2014\0101\c231183-20281182.txt
processing:E:\workspace\python_space\2014\0101\c231184-20279720.txt
processing:E:\workspace\python_space\2014\0101\c231184-20280116.txt
processing:E:\workspace\python_space\2014\0101\c231184-20280894.txt
processing:E:\workspace\python_space\2014\0101\c231184-20280899.txt
processing:E:\workspace\python_space\2014\0101\c

processing:E:\workspace\python_space\2014\0101\c345167-20280844.txt
processing:E:\workspace\python_space\2014\0101\c345167-20280848.txt
processing:E:\workspace\python_space\2014\0101\c345167-20280858.txt
processing:E:\workspace\python_space\2014\0101\c345167-20280862.txt
processing:E:\workspace\python_space\2014\0101\c345167-20280909.txt
processing:E:\workspace\python_space\2014\0101\c345167-20280914.txt
processing:E:\workspace\python_space\2014\0101\c345167-20280918.txt
processing:E:\workspace\python_space\2014\0101\c345167-20280933.txt
processing:E:\workspace\python_space\2014\0101\c345167-20280935.txt
processing:E:\workspace\python_space\2014\0101\c345167-20280956.txt
processing:E:\workspace\python_space\2014\0101\c345167-20280962.txt
processing:E:\workspace\python_space\2014\0101\c345167-20281109.txt
processing:E:\workspace\python_space\2014\0101\c345167-20281113.txt
processing:E:\workspace\python_space\2014\0101\c345167-20281117.txt
processing:E:\workspace\python_space\2014\0101\c

processing:E:\workspace\python_space\2014\0102\c1011-24003794.txt
processing:E:\workspace\python_space\2014\0102\c1011-24004176.txt
processing:E:\workspace\python_space\2014\0102\c1012-24005780.txt
processing:E:\workspace\python_space\2014\0102\c134768-20282540.txt
processing:E:\workspace\python_space\2014\0102\c134768-20282567.txt
processing:E:\workspace\python_space\2014\0102\c134768-20282590.txt
processing:E:\workspace\python_space\2014\0102\c134768-20282722.txt
processing:E:\workspace\python_space\2014\0102\c134768-20282759.txt
processing:E:\workspace\python_space\2014\0102\c134768-20282763.txt
processing:E:\workspace\python_space\2014\0102\c134768-20282934.txt
processing:E:\workspace\python_space\2014\0102\c134768-20282956.txt
processing:E:\workspace\python_space\2014\0102\c134768-20283003.txt
processing:E:\workspace\python_space\2014\0102\c134768-20284399.txt
processing:E:\workspace\python_space\2014\0102\c134768-20285337.txt
processing:E:\workspace\python_space\2014\0102\c134768

...

processing:E:\workspace\python_space\2014\0123\c345454-20457759.txt
processing:E:\workspace\python_space\2014\0123\c345456-20460369.txt
processing:E:\workspace\python_space\2014\0123\c345456-20460377.txt
processing:E:\workspace\python_space\2014\0123\c345456-20460383.txt
processing:E:\workspace\python_space\2014\0123\c345456-20460448.txt
processing:E:\workspace\python_space\2014\0123\c345459-20457570.txt
processing:E:\workspace\python_space\2014\0123\c345459-20457620.txt
processing:E:\workspace\python_space\2014\0123\c345459-20458322.txt
processing:E:\workspace\python_space\2014\0123\c345459-20458374.txt
processing:E:\workspace\python_space\2014\0123\c345459-20458437.txt
processing:E:\workspace\python_space\2014\0123\c345459-20458470.txt
processing:E:\workspace\python_space\2014\0123\c345459-20458705.txt
processing:E:\workspace\python_space\2014\0123\c345459-20459118.txt
processing:E:\workspace\python_space\2014\0123\c345459-20461290.txt
processing:E:\workspace\python_space\2014\0123\c

processing:E:\workspace\python_space\2014\0123\c350648-20459317.txt
processing:E:\workspace\python_space\2014\0123\c350648-20459495.txt
processing:E:\workspace\python_space\2014\0123\c350726-20461774.txt
processing:E:\workspace\python_space\2014\0123\c351992-20459839.txt
processing:E:\workspace\python_space\2014\0123\c352906-20458059.txt
processing:E:\workspace\python_space\2014\0123\c352906-20458444.txt
processing:E:\workspace\python_space\2014\0123\c352906-20459966.txt
processing:E:\workspace\python_space\2014\0123\c352906-20459974.txt
processing:E:\workspace\python_space\2014\0123\c352906-20459977.txt
processing:E:\workspace\python_space\2014\0123\c352908-20460178.txt
processing:E:\workspace\python_space\2014\0123\c352910-20458498.txt
processing:E:\workspace\python_space\2014\0123\c352911-20457657.txt
processing:E:\workspace\python_space\2014\0123\c352911-20459295.txt
processing:E:\workspace\python_space\2014\0123\c352911-20460042.txt
processing:E:\workspace\python_space\2014\0123\c

processing:E:\workspace\python_space\2014\0123\c356312-20457531.txt
processing:E:\workspace\python_space\2014\0123\c356312-20457815.txt
processing:E:\workspace\python_space\2014\0123\c356312-20457875.txt
processing:E:\workspace\python_space\2014\0123\c356312-20458302.txt
processing:E:\workspace\python_space\2014\0123\c356312-20458415.txt
processing:E:\workspace\python_space\2014\0123\c356312-20458511.txt
processing:E:\workspace\python_space\2014\0123\c356312-20458601.txt
processing:E:\workspace\python_space\2014\0123\c356312-20458652.txt
processing:E:\workspace\python_space\2014\0123\c356312-20459043.txt
processing:E:\workspace\python_space\2014\0123\c356312-20459272.txt
processing:E:\workspace\python_space\2014\0123\c356312-20459652.txt
processing:E:\workspace\python_space\2014\0123\c356312-20459653.txt
processing:E:\workspace\python_space\2014\0123\c356312-20459753.txt
processing:E:\workspace\python_space\2014\0123\c356312-20459770.txt
processing:E:\workspace\python_space\2014\0123\c

processing:E:\workspace\python_space\2014\0123\c358314-20456382.txt
processing:E:\workspace\python_space\2014\0123\c358314-20456928.txt
processing:E:\workspace\python_space\2014\0123\c358314-20457745.txt
processing:E:\workspace\python_space\2014\0123\c358314-20457789.txt
processing:E:\workspace\python_space\2014\0123\c358314-20458730.txt
processing:E:\workspace\python_space\2014\0123\c358314-20458892.txt
processing:E:\workspace\python_space\2014\0123\c358314-20458913.txt
processing:E:\workspace\python_space\2014\0123\c358314-20459067.txt
processing:E:\workspace\python_space\2014\0123\c358314-20459140.txt
processing:E:\workspace\python_space\2014\0123\c358314-20459188.txt
processing:E:\workspace\python_space\2014\0123\c358314-20459323.txt
processing:E:\workspace\python_space\2014\0123\c358314-20459343.txt
processing:E:\workspace\python_space\2014\0123\c358314-20459680.txt
processing:E:\workspace\python_space\2014\0123\c358314-20459713.txt
processing:E:\workspace\python_space\2014\0123\c

processing:E:\workspace\python_space\2014\0123\c358428-20455594.txt
processing:E:\workspace\python_space\2014\0123\c358428-20455596.txt
processing:E:\workspace\python_space\2014\0123\c358428-20455598.txt
processing:E:\workspace\python_space\2014\0123\c358428-20455599.txt
processing:E:\workspace\python_space\2014\0123\c358428-20455604.txt
processing:E:\workspace\python_space\2014\0123\c358428-20455627.txt
processing:E:\workspace\python_space\2014\0123\c358428-20455628.txt
processing:E:\workspace\python_space\2014\0123\c358428-20457271.txt
processing:E:\workspace\python_space\2014\0123\c358428-20457416.txt
processing:E:\workspace\python_space\2014\0123\c358428-20458735.txt
processing:E:\workspace\python_space\2014\0123\c358428-20459003.txt
processing:E:\workspace\python_space\2014\0123\c358428-20459801.txt
processing:E:\workspace\python_space\2014\0123\c358428-20461849.txt
processing:E:\workspace\python_space\2014\0123\c358428-20461861.txt
processing:E:\workspace\python_space\2014\0123\c

In [5]:
from collections import Counter
counts_w = Counter(data.words)
vocab_w = sorted(counts_w, key=counts_w.get, reverse=True)
vocab_to_int_w = {word: ii for ii, word in enumerate(vocab_w, 1)}

words_ints = []
lables_ints = []
for each in data.all_sentences:
    words_ints.append([vocab_to_int_w[word] for word in each])    # 生成word2id
for each in data.all_labels:
    lables_ints.append([vocab_to_int_l[label] for label in each]) # 生成label2id

In [77]:
# sentence_lens = Counter([len(x) for x in words_ints])
# print("Zero-length sentence: {}".format(sentence_lens[0]))
# print("Maximum sentence length: {}".format(max(sentence_lens)))
# labels_lens = Counter([len(x) for x in lables_ints])
# print("Zero-length label: {}".format(labels_lens[0]))
# print("Maximum label length: {}".format(max(labels_lens)))

Zero-length sentence: 76
Maximum sentence length: 571
Zero-length label: 76
Maximum label length: 571


In [6]:
# 删除空句
non_zero_idx = [ii for ii, sent in enumerate(words_ints) if len(sent) != 0] 
len(non_zero_idx)

429162

In [7]:
words_ints = [words_ints[ii] for ii in non_zero_idx]
lables_ints = [lables_ints[ii] for ii in non_zero_idx]

In [11]:
# padding
seq_len = 200
features_ = np.zeros((len(words_ints), seq_len), dtype=int)
labels_ = np.zeros((len(lables_ints), seq_len), dtype=int)

for i, row in enumerate(words_ints):
    features_[i, :len(row)] = np.array(row)[:seq_len]
for i, row in enumerate(lables_ints):
    labels_[i, :len(row)] = np.array(row)[:seq_len]

In [12]:
features_[0]

array([  475,  2731,  1785,    73,    25,  1772,  1318,    24,   122,
           1,   108, 11375,  6866,     7,   171,     2,   483,   903,
         352,   956,     1,    10,   812,  6866,   519,     1,    27,
          52,   651,  3051,   121,  2130,   651,  3051,   938,   623,
         135,     2,   886,     3,     0,     0,     0,     0,     0,
           0,     0,     0,     0,     0,     0,     0,     0,     0,
           0,     0,     0,     0,     0,     0,     0,     0,     0,
           0,     0,     0,     0,     0,     0,     0,     0,     0,
           0,     0,     0,     0,     0,     0,     0,     0,     0,
           0,     0,     0,     0,     0,     0,     0,     0,     0,
           0,     0,     0,     0,     0,     0,     0,     0,     0,
           0,     0,     0,     0,     0,     0,     0,     0,     0,
           0,     0,     0,     0,     0,     0,     0,     0,     0,
           0,     0,     0,     0,     0,     0,     0,     0,     0,
           0,     0,

In [13]:
save_p =  'E:\\workspace\\python_space\\NLP-tools\\data\\Seg_data.pkl'
with open(save_p, 'wb') as outp:
    pickle.dump(features_, outp)
    pickle.dump(labels_, outp)
    pickle.dump(vocab_to_int_w, outp)
    pickle.dump(vocab_to_int_l, outp)
    print('** Finished saving the data.')

** Finished saving the data.


## 数据格式

In [13]:
save_path =  'E:\\workspace\\python_space\\NLP-tools\\data\\Seg_data.pkl'
with open(save_path, 'rb') as inp:
    X = pickle.load(inp)
    y = pickle.load(inp)
    word2id = pickle.load(inp)
    tag2id = pickle.load(inp)

In [17]:
print(X[0])

[    0     0     0     0     0     0     0     0     0     0     0     0
     0     0     0     0     0     0     0     0     0     0     0     0
     0     0     0     0     0     0     0     0     0     0     0     0
     0     0     0     0     0     0     0     0     0     0     0     0
     0     0     0     0     0     0     0     0     0     0     0     0
     0     0     0     0     0     0     0     0     0     0     0     0
     0     0     0     0     0     0     0     0     0     0     0     0
     0     0     0     0     0     0     0     0     0     0     0     0
     0     0     0     0     0     0     0     0     0     0     0     0
     0     0     0     0     0     0     0     0     0     0     0     0
     0     0     0     0     0     0     0     0     0     0     0     0
     0     0     0     0     0     0     0     0     0     0     0     0
     0     0     0     0     0     0     0     0     0     0     0     0
     0     0     0     0   475  2731  1785    73   

In [18]:
len(y[0])

200

## 测试集测试

In [1]:
#encoding=utf8
import re
import os
import numpy as np
import tensorflow as tf
import data_read as readData
import bi_lstm_model as modelDef
from tensorflow.contrib import crf

c:\users\admin\anaconda3\lib\site-packages\h5py\__init__.py:34: FutureWarning: Conversion of the second argument of issubdtype from `float` to `np.floating` is deprecated. In future, it will be treated as `np.float64 == np.dtype(float).type`.
  from ._conv import register_converters as _register_converters


In [2]:
data = readData.DataHandler(save_path = 'data/Seg_data.pkl')
data.loadData()

In [3]:
data_train, data_valid, data_test = data.builderTrainData()

X_train.shape=(274663, 200), y_train.shape=(274663, 200); 
X_valid.shape=(68666, 200), y_valid.shape=(68666, 200);
X_test.shape=(85833, 200), y_test.shape=(85833, 200)
Creating the data generator ...
Finished creating the data generator.


In [4]:
model = modelDef.BiLSTMModel(max_len=data.max_len, vocab_size=data.word2id.__len__(), class_num= data.tag2id.__len__())

(?, 148)
(?, 200, 148)


c:\users\admin\anaconda3\lib\site-packages\tensorflow\python\ops\gradients_impl.py:96: UserWarning: Converting sparse IndexedSlices to a dense Tensor of unknown shape. This may consume a large amount of memory.
  "Converting sparse IndexedSlices to a dense Tensor of unknown shape. "


Finished training the bi-lstm model.


In [5]:
sess = tf.Session()
ckpt = tf.train.latest_checkpoint('.\ckpt')
print(ckpt)
saver = tf.train.Saver()
if ckpt:
    saver.restore(sess, ckpt)

.\ckpt\pos.ckpt-6
INFO:tensorflow:Restoring parameters from .\ckpt\pos.ckpt-6


In [15]:
X_batch, y_batch = data_test.next_batch(1)

In [16]:
X_batch

array([[   28,  1488,   229,   172,   516,  9293,  9725,  1734,   109,
         1237,  9753, 16669,  3173,     0,     0,     0,     0,     0,
            0,     0,     0,     0,     0,     0,     0,     0,     0,
            0,     0,     0,     0,     0,     0,     0,     0,     0,
            0,     0,     0,     0,     0,     0,     0,     0,     0,
            0,     0,     0,     0,     0,     0,     0,     0,     0,
            0,     0,     0,     0,     0,     0,     0,     0,     0,
            0,     0,     0,     0,     0,     0,     0,     0,     0,
            0,     0,     0,     0,     0,     0,     0,     0,     0,
            0,     0,     0,     0,     0,     0,     0,     0,     0,
            0,     0,     0,     0,     0,     0,     0,     0,     0,
            0,     0,     0,     0,     0,     0,     0,     0,     0,
            0,     0,     0,     0,     0,     0,     0,     0,     0,
            0,     0,     0,     0,     0,     0,     0,     0,     0,
      

In [17]:
y_batch

array([[ 76, 116,  31,  80, 116, 116,  41, 116,  31, 116,  12, 120, 120,
          0,   0,   0,   0,   0,   0,   0,   0,   0,   0,   0,   0,   0,
          0,   0,   0,   0,   0,   0,   0,   0,   0,   0,   0,   0,   0,
          0,   0,   0,   0,   0,   0,   0,   0,   0,   0,   0,   0,   0,
          0,   0,   0,   0,   0,   0,   0,   0,   0,   0,   0,   0,   0,
          0,   0,   0,   0,   0,   0,   0,   0,   0,   0,   0,   0,   0,
          0,   0,   0,   0,   0,   0,   0,   0,   0,   0,   0,   0,   0,
          0,   0,   0,   0,   0,   0,   0,   0,   0,   0,   0,   0,   0,
          0,   0,   0,   0,   0,   0,   0,   0,   0,   0,   0,   0,   0,
          0,   0,   0,   0,   0,   0,   0,   0,   0,   0,   0,   0,   0,
          0,   0,   0,   0,   0,   0,   0,   0,   0,   0,   0,   0,   0,
          0,   0,   0,   0,   0,   0,   0,   0,   0,   0,   0,   0,   0,
          0,   0,   0,   0,   0,   0,   0,   0,   0,   0,   0,   0,   0,
          0,   0,   0,   0,   0,   0,   0,   0,   0

In [18]:
fetches = [model.scores, model.length, model.transition_params]
feed_dict = {model.X_inputs: X_batch, model.lr: 1.0, model.batch_size: 1,
             model.keep_prob: 1.0}
test_score, test_length, transition_params = sess.run(fetches, feed_dict)
tags, _ = crf.viterbi_decode(test_score[0][:test_length[0]], transition_params)
print(tags)

[76, 116, 31, 80, 116, 116, 41, 116, 31, 116, 12, 120, 120]


In [25]:
import pandas as pd

test_file='.\\test\\seg_result.txt'
test_result='.\\test\pos_result.txt'

pos = pd.read_csv('./pos.csv')
id2tag = {ii: label for ii, label in enumerate(list(pos['POS']),1)}
id2tag[0]=''

isFile = os.path.isfile(test_file)
if isFile:
    with open(test_result, "w", encoding='utf-8') as out:  # 读写文件默认都是UTF-8编码的
        with open(test_file, "r", encoding='utf-8') as fp:
            for line in fp.readlines(): # line 段

                words_ints = []
                word_ints = []  
                line = line.strip()
                line = line.replace('/ ','').replace('/Date ','').replace('/','')
                line = line.strip()
                word_ = line.split(' ')
                
                for word in word_:
                    if word in data.word2id:
                        word_ints.append(data.word2id[word])
                    else:
                        word_ints.append('126')
                words_ints.append(word_ints)
                seq_len = 200
                features_ = np.zeros((len(words_ints), seq_len), dtype=int)
                for i, row in enumerate(words_ints):
                    features_[i, :len(row)] = np.array(row)[:seq_len]

                # features_ 已验证                          
                X_batch = features_ 

                fetches = [model.scores, model.length, model.transition_params]
                feed_dict = {model.X_inputs: X_batch, model.lr: 1.0, model.batch_size: 1,
                             model.keep_prob: 1.0}
                test_score, test_length, transition_params = sess.run(fetches, feed_dict)
                tags, _ = crf.viterbi_decode(test_score[0][:test_length[0]], transition_params)

                tags = [id2tag[i] for i in tags]

                result = ''
                for i in range(len(word_)):
                    result = result + word_[i] + '/' +tags[i] + ' '
                
                out.write("%s\n" % (result))

['\ufeff', '人民网', '莫斯科', '1月9日', '电', '（', '记者', '刘旭', '）', '据', '来自', '俄罗斯', '政府', '网站', '的', '消息', '，', '俄政府', '总理', '梅德韦杰夫', '向', '教育', '科学部', '长里瓦诺夫', '下令', '，', '高等', '院校', '在', '2014年', '新学', '年', '录取', '新生', '时', '，', '应', '把', '中学生', '的', '毕业', '考试', '成绩', '与', '国家', '统一', '考试', '成绩', '一起', '列入', '考核', '因素', '。']
['梅德韦杰夫', '在', '命令', '中', '还', '让', '俄罗斯', '联邦', '教育', '科学部', '保障', '举办', '国家', '统一', '考试', '的', '考点', '，', '定出', '让', '大学生', '可能', '接受', '的', '住宿费', '，', '以及', '提高', '外国', '学生', '的', '学习', '效率', '等', '。', '此外', '，', '俄', '总理', '还', '委托', '俄罗斯', '教育', '科学部', '“', '制定', '并', '核准', '一套', '完善', '中学生', '对', '未来', '职业', '选择', '的', '措施', '。', '”']


In [24]:
X_batch

array([[41631,     7,  5454,    14,    38,    53,   957,  3958,   223,
          126,   390,  1131,    96,   663,   853,     2, 10290,     1,
          126,    53,  2071,   214,   278,     2,  8383,     1,   234,
          291,  2853,   297,     2,   536,  2505,    22,     3,   490,
            1,  2283,  2379,    38,  3288,   957,   223,   126,     5,
          813,    50,  6122,  2639,   537, 11264,    20,   635,  1257,
          387,     2,   462,     3,     6,     0,     0,     0,     0,
            0,     0,     0,     0,     0,     0,     0,     0,     0,
            0,     0,     0,     0,     0,     0,     0,     0,     0,
            0,     0,     0,     0,     0,     0,     0,     0,     0,
            0,     0,     0,     0,     0,     0,     0,     0,     0,
            0,     0,     0,     0,     0,     0,     0,     0,     0,
            0,     0,     0,     0,     0,     0,     0,     0,     0,
            0,     0,     0,     0,     0,     0,     0,     0,     0,
      